In [129]:
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2

In [130]:
with open('stopwords_zh.txt', 'r') as file:
    stopwords = file.read().splitlines() 
file.close()

In [131]:
df_stock = pd.DataFrame()
for i in range(2021, 2024):
    x = pd.read_excel("../../bda2023_mid_dataset/stock_data_2019-2023.xlsx", sheet_name=f'上市{i}', usecols=['證券代碼', '年月日', '收盤價(元)'])
    x = x[x['證券代碼'] == '2330 台積電']
    x = x.loc[::-1]
    df_stock = pd.concat([df_stock, x])

In [132]:
df_stock = df_stock.reset_index(drop = True)
df_stock

證券代碼         年月日    收盤價(元)
0    2330 台積電  2021/01/04  526.7744
1    2330 台積電  2021/01/05  532.6711
2    2330 台積電  2021/01/06  539.5506
3    2330 台積電  2021/01/07  555.2752
4    2330 台積電  2021/01/08  570.0170
..        ...         ...       ...
534  2330 台積電  2023/03/20  512.0000
535  2330 台積電  2023/03/21  517.0000
536  2330 台積電  2023/03/22  533.0000
537  2330 台積電  2023/03/23  538.0000
538  2330 台積電  2023/03/24  539.0000

[539 rows x 3 columns]

In [133]:
label = []
for i in range(len(df_stock) - 3):
    rate = (df_stock['收盤價(元)'][i + 3] - df_stock['收盤價(元)'][i]) / df_stock['收盤價(元)'][i]
    if rate > 0.01:
       label.append('漲')
    elif rate < -0.01:
        label.append('跌')
    else:
        label.append('持平')

label.extend([0, 0, 0])
df_stock['label'] = label
df_stock.tail(10)

證券代碼         年月日    收盤價(元) label
529  2330 台積電  2023/03/13  513.2229     跌
530  2330 台積電  2023/03/14  507.2552     漲
531  2330 台積電  2023/03/15  508.2498    持平
532  2330 台積電  2023/03/16  505.0000     漲
533  2330 台積電  2023/03/17  518.0000     漲
534  2330 台積電  2023/03/20  512.0000     漲
535  2330 台積電  2023/03/21  517.0000     漲
536  2330 台積電  2023/03/22  533.0000     0
537  2330 台積電  2023/03/23  538.0000     0
538  2330 台積電  2023/03/24  539.0000     0

In [134]:
df_stock['年月日'] = pd.to_datetime(df_stock['年月日']).dt.date
df_stock.tail(10)

證券代碼         年月日    收盤價(元) label
529  2330 台積電  2023-03-13  513.2229     跌
530  2330 台積電  2023-03-14  507.2552     漲
531  2330 台積電  2023-03-15  508.2498    持平
532  2330 台積電  2023-03-16  505.0000     漲
533  2330 台積電  2023-03-17  518.0000     漲
534  2330 台積電  2023-03-20  512.0000     漲
535  2330 台積電  2023-03-21  517.0000     漲
536  2330 台積電  2023-03-22  533.0000     0
537  2330 台積電  2023-03-23  538.0000     0
538  2330 台積電  2023-03-24  539.0000     0

In [135]:
upCnt = 0
downCnt = 0
for i in range(len(df_stock)):
    if df_stock['label'][i] == '漲':
        upCnt += 1
    elif df_stock['label'][i] == '跌':
        downCnt += 1 
print('預估漲的天數：', upCnt)
print('預估跌的天數：', downCnt)

預估漲的天數： 180
預估跌的天數： 200


In [136]:
df_news = pd.read_excel("../../TSMC_news_21-23.xlsx")
df_news.head()

Unnamed: 0  post_time                         title  \
0           0 2021-01-01  明年買哪幾檔晶片股?分析師首選 Nvidia 和 AMD   
1           1 2021-01-01             《大陸產業》中芯成熟製程 獲美放行   
2           2 2021-01-04        《各報要聞》台積今年資本支出上看200億美元   
3           3 2021-01-04     《半導體》台積電等供應鏈力挺 聯發科Q1拚淡季不淡   
4           4 2021-01-04           《半導體》2021年拚翻身 創意鎖漲停   

                                             content  \
0  週四 (31 日) 華爾街分析師表示，Nvidia 和 AMD 本月漲勢落後於其他半導體類股...   
1  【時報-台北電】遭美制裁的大陸晶圓代工龍頭中芯國際迎來曙光。業界傳出，中芯國際成熟製程獲得美...   
2  【時報-台北電】晶圓代工龍頭台積電2020年繳出亮麗成績單，預期全年美元營收年成長率逾三成並...   
3  【時報記者王逸芯台北報導】聯發科(2454)在去年第三季一舉超車高通，在行動晶片市占率衝上3...   
4  【時報記者王逸芯台北報導】創意(3443)營運最壞時期已經過去，去年第四季在NRE案認列入帳...   

                                               token  
0  ['週四', '日', '華爾街', '分析師', '表示', '和', '本', '月',...  
1  ['時報', '台北電', '遭', '美', '制裁', '的', '大陸', '晶圓',...  
2  ['時報', '台北', '電', '晶圓', '代工', '龍頭', '台積電', '年'...  
3  ['時報', '記者', '王逸芯', '台北', '報導', '聯發科', '在', '去...  
4  ['時報', '記者', '王逸芯', '台北', '報導', '創意', '營運', '最...

In [137]:
label_news = []
for i in range(len(df_news)):
    for j in range(len(df_stock)):
        if df_news['post_time'][i] == df_stock['年月日'][j]:
            label_news.append(df_stock['label'][j])
    if len(label_news) == i:
        label_news.append(0) # 日期沒有對到的情況（e.g. 週末） 

df_news['label'] = label_news
df_news.head(10)
df_news.tail(10)

/var/folders/mn/3mpydyqj1tq0wy92y446smg80000gn/T/ipykernel_1823/430857461.py:4: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  if df_news['post_time'][i] == df_stock['年月日'][j]:


Unnamed: 0  post_time                                  title  \
6822        6822 2023-03-20                           算力大戰 台積日月光受惠   
6823        6823 2023-03-20    銀行股再見殺氣，美股四巫日齊黑，道瓊急跌385點，微軟逆勢漲約1.2%   
6824        6824 2023-03-20             《熱門族群》外資釋出AI口袋名單股 台積電等3檔入列   
6825        6825 2023-03-20      台積電蟬聯百大創新企業，專利與營業秘密雙軌保護成果，研發營收比8%   
6826        6826 2023-03-20  台積電／台積電「創新」再獲獎 副法務長陳碧莉：去年在台、美專利獲准百發百中   
6827        6827 2023-03-21               晶片業起死回生？日媒揭實際庫存真相：反轉訊號來了   
6828        6828 2023-03-21          《盤前掃瞄-基本面》高通加速轉單台灣；國發會估景氣4月探底   
6829        6829 2023-03-21                     《各報要聞》高通去中化 加速轉單台灣   
6830        6830 2023-03-21                       《科技》台積電兩招…擴大專利版圖   
6831        6831 2023-03-21             《熱門族群》高通轉單喜訊 精測笑開懷、這兩檔卻擺臭臉   

                                                content  \
6822  隨著微軟轉投資OpenAI推出的聊天機器人ChatGPT全球爆紅，包括Google、阿里巴巴...   
6823  【財訊快報／陳孟朔】被華府接管的矽谷銀行(SVB)，其母公司SVB金融集團申請破產保護的同時...   
6824  【時報記者王逸芯台北報導】ChatGPT颳起AI旋風，美系外資針對AI產業也出具最新研究報告...   
6825  【財訊快報／記者李純君報導】台積電(2330)今年繼續蟬聯百大創新企業，其副法務長陳碧莉提到...   
6826  台積電（2330）再次入選「2023全球百大創新機構獎」，出席領獎的台積電副法務漲陳碧莉表示...   
6827  半導體景氣反轉向下，從「供不應求」轉變成「供應過剩」，市場關注產業景氣何時才會翻轉向上，日媒...   
6828  【時報-台北電】基本面：1.前一交易日新台幣以30.593元兌一美元收市，貶值3.9分，成交...   
6829  【時報-台北電】為了因應半導體市場出現美國陣營及中國陣營的兩極化地緣政治風險，手機晶片大廠高...   
6830  【時報-台北電】晶圓代工龍頭台積電20日獲頒2023年科睿唯安全球百大創新機構獎，副法務長陳...   
6831  【時報-台北電】台股今日隨美股彈升，在金融股回神、AI等具題材族群續強下，大盤指數盤中彈升約...   

                                                  token label  
6822  ['隨著', '微軟', '轉', '投資', '推出', '的', '聊天', '機器人'...     漲  
6823  ['財訊', '快報', '陳孟朔', '被', '華府', '接管', '的', '矽谷銀...     漲  
6824  ['時報', '記者', '王逸芯', '台北', '報導', '颳起', '旋風', '美...     漲  
6825  ['財訊快報', '記者', '李純君', '報導', '台積電', '今年', '繼續',...     漲  
6826  ['台積電', '再次', '入選', '全球', '百', '大', '創新', '機構獎...     漲  
6827  ['半導體', '景氣', '反轉', '向', '下', '從', '供', '不', '...     漲  
6828  ['時報', '台北', '電', '基本面', '前', '一', '交易日', '新台幣...     漲  
6829  ['時報', '台北電', '為了', '因應', '半導體', '市場', '出現', '...     漲  
6830  ['時報', '台北', '電晶圓', '代工', '龍頭', '台積電', '日', '獲...     漲  
6831  ['時報', '台北電', '台股', '今日', '隨', '美股', '彈升', '在'...     漲

In [138]:
#刪掉 label 是 0 的資料
df_news_no_zero = df_news[df_news.label != 0]
df_news_no_zero = df_news_no_zero.reset_index(drop = True)

In [139]:
#token 型態轉換，fit in 套件
df_news_list = []
for i in range(len(df_news_no_zero)):
    df_news_list_tmp = []
    df_news_str = ''
    df_news_list_tmp = eval(df_news_no_zero.token[i])
    df_news_str = ' '.join(df_news_list_tmp)
    df_news_list.append(df_news_str)
df_news_list

['時報 台北 電 晶圓 代工 龍頭 台積電 年 繳出 亮麗 成績單 預期 全 年 美元 營收 年 成長率 逾 三成 並 創下 歷史 新高年 雖然 仍 有 新冠 肺炎 疫情 蔓延 地緣 政治 及 貿易戰 等 外在 環境 變數 但 晶圓 代工 訂單 強勁 第二季 前 產能 利用率 維持 滿載 設備 業者 及 市場 法人 看好 台積電 年 奈米 產能 建置 及 奈米 技術 研發 加速 進行 全 年 資本 支出 將 上看 億 美元 再 創 新高 台積電 年 資本 支出 估 達 億 美元 創下 新高 無虞 但 奈米 及 奈米 等 先 進 製程 奈米 以上 成熟 製程 等 產能 仍 供 不 應 求 台積電 年 持續 擴增 產能 以 因應 強勁 需求 包括 廠 第三 期 奈米 產能 將 在 第一季 開出 廠 奈米 產能 建置 正 加速 進行 同時 提升 奈米 閘極 全 球 場效電 晶體 技術 研發 速度 等 設備 業者 指出 受惠 於 及 人工 智慧 及 高效能 運算車 用 及 物聯網 晶片 等 晶圓 代工 需求 強勁 台積電 看 好 年 產能 持續 供 不 應求 奈米 及 奈米 接單 幾乎 全 滿成熟 製程 產能 全 線 吃緊 加上 奈米 產能 建置 及 美國 奈米 新廠 動工 將 同步 展開 持續 增加 極 紫外光 曝光機 及 相關 設備 採購 規模 預期年 資本 支出 將 上看 億 美元 連續 三年 創下 歷史 新高 以 年 新廠 建置 進度 來 看 台積電 針對 奈米 製程 打造 的 廠 共 三 期 工程 已 動工 美國 奈米 建廠 即將 展開 南科 廠會 再 興建 廠 做為 特殊 製程 晶圓廠 並 在 同 一 廠 區 內 興建 先進 封裝 技術 生產 基地 再者 竹科 廠區 將 興建 擁有 兩 座 研發晶圓廠 的 研發中心 其中 研發 晶圓廠 預 計年 完工 做為 奈米 及 更 先進 製程 的 研發 基地 竹南 先進 封裝廠 則 如期 進行 台積電 奈米 將 於 年 第二季 進入 量產 及 應用 會 是 主要 產品線 根據 台積電 規畫 奈米 晶圓廠 廠 房 基地 面積 約 為 公頃 潔淨室 面積 將 超過 萬 平方 公尺 大約 是 座 標準 足球場 大小 奈米 進入 量產 時 當年 產能 預估 將 超過 每 年 萬 片 吋 晶圓 業界 預期 台積電 會 是 全球 第

In [153]:
#將所有資料向量化，轉成 tfidf vector
vectorizer = TfidfVectorizer(stop_words=stopwords)
X_train = vectorizer.fit_transform(df_news_list)
X_train = pd.DataFrame(X_train.toarray(),columns=vectorizer.get_feature_names_out())
X_train

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['lex', '①①', '①②', '①③', '①④', '①⑤', '①⑥', '①⑦', '①⑧', '①⑨', '①ａ', '①ｂ', '①ｃ', '①ｄ', '①ｅ', '①ｆ', '①ｇ', '①ｈ', '①ｉ', '①ｏ', '②①', '②②', '②③', '②④', '②⑤', '②⑥', '②⑦', '②⑧', '②⑩', '②ａ', '②ｂ', '②ｄ', '②ｅ', '②ｆ', '②ｇ', '②ｈ', '②ｉ', '②ｊ', '③①', '③⑩', '③ａ', '③ｂ', '③ｃ', '③ｄ', '③ｅ', '③ｆ', '③ｇ', '③ｈ', '④ａ', '④ｂ', '④ｃ', '④ｄ', '④ｅ', '⑤ａ', '⑤ｂ', '⑤ｄ', '⑤ｅ', '⑤ｆ', '１２', 'ｌｉ', 'ｚｘｆｉｔｌ'] not in stop_words.
  warnings.warn(


一一一億  一一七五  一一七八  一一七六億  一一九九七  一一五  一一兆  一一八五  一一六  一一六億  ...   龐然  \
0      0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
1      0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
2      0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
3      0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
4      0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
...    ...   ...   ...    ...    ...  ...  ...   ...  ...   ...  ...  ...   
6149   0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
6150   0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
6151   0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
6152   0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   
6153   0.0   0.0   0.0    0.0    0.0  0.0  0.0   0.0  0.0   0.0  ...  0.0   

       龐雜  龔培元  龔明鑫  龔明鑫日   龔說   龜尾   龜山  龜山廠   龜牙  
0     0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
1     0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
2     0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
3     0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
4     0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
...   ...  ...  ...   ...  ...  ...  ...  ...  ...  
6149  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
6150  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
6151  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
6152  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  
6153  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  

[6154 rows x 71305 columns]

In [154]:
y_train = df_news_no_zero['label']

chi2_selector = SelectKBest(chi2, k = 2000)
chi2_selector.fit(X_train, y_train)
kbest_vocabs = X_train.columns[chi2_selector.get_support()]
X_train = X_train[kbest_vocabs]
X_train

一角  七利多   七黑   三多  三王弱  三萬三   上代  上千金   上午   上品  ...  鼎權證  鼎錢景  齊減碼  \
0     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
1     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
2     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
3     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
4     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
...   ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
6149  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
6150  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
6151  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
6152  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
6153  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   

      齊發聯發科   齊締   齊讚   齊賀   龍潭  龍頭市  龐佩奧  
0       0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1       0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2       0.0  0.0  0.0  0.0  0.0  0.0  0.0  
3       0.0  0.0  0.0  0.0  0.0  0.0  0.0  
4       0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...     ...  ...  ...  ...  ...  ...  ...  
6149    0.0  0.0  0.0  0.0  0.0  0.0  0.0  
6150    0.0  0.0  0.0  0.0  0.0  0.0  0.0  
6151    0.0  0.0  0.0  0.0  0.0  0.0  0.0  
6152    0.0  0.0  0.0  0.0  0.0  0.0  0.0  
6153    0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[6154 rows x 2000 columns]

In [155]:
#隨資切分資料，train 80%、test 20%
from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split(X_train, y_train, test_size = 0.2, random_state = 1, stratify = y_train)

In [157]:
print('x len', len(X_train), 'y len', len(Y_train))
print('x len', len(X_test), 'y len', len(Y_test))

x len 4923 y len 4923
x len 1231 y len 1231


In [163]:
#建立預測模型（NB 牛逼演算法）
from sklearn.naive_bayes import BernoulliNB
from sklearn import metrics
NB_model = BernoulliNB()

In [165]:
NB_model.fit(X_train,Y_train)

BernoulliNB()

In [166]:
predicted_results = []
expected_results = []
expected_results.extend(Y_test)
predicted_results.extend(NB_model.predict(X_test))
print(predicted_results)

['跌', '漲', '持平', '漲', '漲', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '漲', '跌', '漲', '跌', '持平', '漲', '跌', '跌', '持平', '跌', '漲', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '持平', '漲', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '持平', '持平', '跌', '跌', '漲', '漲', '跌', '跌', '跌', '持平', '漲', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '漲', '跌', '持平', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '持平', '跌', '跌', '持平', '持平', '漲', '跌', '跌', '漲', '持平', '漲', '跌', '漲', '持平', '跌', '漲', '跌', '持平', '漲', '持平', '漲', '跌', '持平', '持平', '持平', '漲', '跌', '漲', '跌', '漲', '持平', '跌', '持平', '跌', '跌', '持平', '漲', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '持平', '漲', '漲', '跌', '跌', '漲', '持平', '持平', '漲', '漲', '持平', '漲', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '漲', '持平', '跌', '漲', '跌', '漲', '跌', '持平', '持平', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '持平', '跌', '漲', '漲', '漲', '漲', '漲', '跌', '持平', '跌', '跌', '跌', '跌', '跌'

In [167]:
report = metrics.classification_report(expected_results, predicted_results)
print(report)

              precision    recall  f1-score   support

          持平       0.57      0.38      0.45       378
           漲       0.60      0.51      0.55       396
           跌       0.53      0.75      0.62       457

    accuracy                           0.56      1231
   macro avg       0.57      0.54      0.54      1231
weighted avg       0.57      0.56      0.55      1231



In [180]:
#建立預測模型（SVM Linear）
from sklearn.svm import SVC
SVM_model = SVC(kernel = 'linear', C = 50.0, probability=True)
SVM_model.fit(X_train,Y_train)

In [ ]:
predicted_results = []
expected_results = []
expected_results.extend(Y_test)
predicted_results.extend(SVM_model.predict(X_test))
print(predicted_results)

['漲', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '漲', '漲', '跌', '漲', '跌', '跌', '持平', '跌', '跌', '漲', '跌', '持平', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '漲', '漲', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '漲', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '漲', '漲', '漲', '跌', '跌', '持平', '漲', '持平', '漲', '跌', '持平', '跌', '跌', '漲', '漲', '持平', '跌', '跌', '跌', '持平', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '持平', '跌', '跌', '跌', '持平', '跌', '跌', '持平', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '跌', '漲', '跌', '跌', '跌', '跌', '漲', '跌', '持平', '跌', '跌', '跌', '漲', '持平', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '漲', '漲', '漲', '跌', '漲', '漲', '跌', '持平', '漲', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '漲', '跌', '跌', '漲', '跌', '漲', '跌', '漲', '持平', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '跌', '跌', '跌', '持平',

In [ ]:
report = metrics.classification_report(expected_results, predicted_results)
print(report)

              precision    recall  f1-score   support

          持平       0.66      0.22      0.34       378
           漲       0.63      0.38      0.47       396
           跌       0.45      0.84      0.58       457

    accuracy                           0.50      1231
   macro avg       0.58      0.48      0.46      1231
weighted avg       0.57      0.50      0.47      1231



In [173]:
#建立預測模型（SVM Rbf）
SVM_model = SVC(kernel = 'rbf', C = 1.0, probability=True)
SVM_model.fit(X_train,Y_train)

SVC(probability=True)

In [175]:
predicted_results = []
expected_results = []
expected_results.extend(Y_test)
predicted_results.extend(SVM_model.predict(X_test))
print(predicted_results)

['漲', '跌', '持平', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '跌', '跌', '漲', '漲', '跌', '持平', '跌', '跌', '漲', '跌', '持平', '跌', '持平', '持平', '跌', '持平', '跌', '跌', '跌', '跌', '漲', '跌', '跌', '跌', '漲', '跌', '漲', '跌', '跌', '跌', '持平', '跌', '持平', '漲', '跌', '漲', '跌', '跌', '漲', '跌', '漲', '持平', '持平', '跌', '跌', '漲', '漲', '漲', '跌', '跌', '持平', '漲', '持平', '漲', '漲', '持平', '持平', '跌', '漲', '漲', '持平', '跌', '跌', '跌', '持平', '跌', '持平', '跌', '跌', '跌', '持平', '漲', '跌', '跌', '持平', '跌', '持平', '跌', '持平', '漲', '跌', '持平', '跌', '漲', '跌', '跌', '跌', '漲', '漲', '跌', '漲', '持平', '跌', '漲', '跌', '漲', '漲', '持平', '持平', '跌', '跌', '漲', '持平', '跌', '跌', '跌', '跌', '持平', '跌', '跌', '跌', '持平', '跌', '跌', '漲', '跌', '跌', '跌', '跌', '跌', '跌', '持平', '漲', '漲', '漲', '跌', '跌', '漲', '跌', '持平', '漲', '跌', '跌', '持平', '跌', '跌', '跌', '持平', '持平', '跌', '持平', '跌', '持平', '跌', '漲', '跌', '跌', '跌', '漲', '持平', '跌', '漲', '跌', '漲', '持平', '持平', '持平', '持平', '跌', '跌', '跌', '跌', '跌', '持平', '持平', '持平', '持平', '持平', '漲', '漲', '跌', '跌', '漲', '跌', '漲', '持平', '跌', '跌', '跌'

In [176]:
report = metrics.classification_report(expected_results, predicted_results)
print(report)

              precision    recall  f1-score   support

          持平       0.64      0.42      0.51       378
           漲       0.62      0.45      0.52       396
           跌       0.52      0.79      0.62       457

    accuracy                           0.57      1231
   macro avg       0.59      0.55      0.55      1231
weighted avg       0.59      0.57      0.55      1231



### 漲

In [144]:
df_up = df_news[df_news['label'] == '漲'] 
df_up = df_up.reset_index(drop = True)
df_up.head() # 漲的文章
df_up.to_excel('upNews21-23.xlsx')

In [145]:
df_up.token

0       ['時報', '台北', '電', '晶圓', '代工', '龍頭', '台積電', '年'...
1       ['時報', '記者', '王逸芯', '台北', '報導', '聯發科', '在', '去...
2       ['時報', '記者', '王逸芯', '台北', '報導', '創意', '營運', '最...
3       ['台股', '今日', '開', '紅盤', '在', '各', '國', '寬鬆', '...
4       ['時報', '台北電台', '積電', '股價', '新年', '正', '開啟', '新...
                              ...                        
1972    ['半導體', '景氣', '反轉', '向', '下', '從', '供', '不', '...
1973    ['時報', '台北', '電', '基本面', '前', '一', '交易日', '新台幣...
1974    ['時報', '台北電', '為了', '因應', '半導體', '市場', '出現', '...
1975    ['時報', '台北', '電晶圓', '代工', '龍頭', '台積電', '日', '獲...
1976    ['時報', '台北電', '台股', '今日', '隨', '美股', '彈升', '在'...
Name: token, Length: 1977, dtype: object

### 跌

In [146]:
df_down = df_news[df_news['label'] == '跌']
df_down = df_down.reset_index(drop = True)
df_down.head() # 跌的文章
df_down.to_excel('downNews21-23.xlsx')

In [147]:
df_down.token

0       ['台股', '盤', '前', '要', '聞', '共有', '九', '大', '重點...
1       ['開盤', '日出刊', '拜登', '就職', '典禮', '市場', '看好', '族...
2       ['中央社', '記者', '張建中', '新竹', '年月', '日', '電', '晶圓...
3       ['時報', '記者', '沈培華', '台北', '報導', '台積電', '與', '聯...
4       ['中央社', '記者', '張建中', '新竹', '年月日', '電', '晶圓', '...
                              ...                        
2281    ['時報', '記者', '林資傑', '台北', '報導', '市場', '研究', '機...
2282    ['根據', '集邦', '科技', '調查', '即使', '半導體', '產業', '遭...
2283    ['在', '積體', '電路', '產業', '的', '領航', '帶動', '下', ...
2284    ['時報', '台北電', '在', '積體', '電路', '產業', '的', '領航'...
2285    ['三星', '近來', '已', '聘請', '台積電', '前', '研發', '主管'...
Name: token, Length: 2286, dtype: object

In [148]:
df_down_list = []
for i in range(len(df_down)):
    df_down_list_tmp = []
    df_down_str = ''
    df_down_list_tmp = eval(df_down.token[i])
    df_down_str = ' '.join(df_down_list_tmp)
    df_down_list.append(df_down_str)
df_down_list

['台股 盤 前 要 聞 共有 九 大 重點 鴻海 傳出 已 打進 供應 鏈 正 趕工 生產 關鍵 零組件 義隆 聚積 合作 研發 拿下 新一代 大單 以及 國內 首 家 純網銀 正式 營運 樂天 推出 兩 大 引擎 以下 是 今日 必 看 重要 財經 新聞 外資 鴻海 已 打進 供應鏈 趕工 生產 關鍵 零組件 鴻海 傳出 已 打入 蘋果 供應 鏈 日系 外資 指出 鴻海 正 積極 趕工 製造 蘋果 需要 的 零組件 有望 成為 長線 營運 引擎 閱讀 全文 義隆聚積 合作 報捷 拿下 新一代 大單 任 天堂 積極 籌備 下一代 遊戲機 傳出 將 採用 新 世代 面板 技術 除了 找上 台 廠群 創 合作 據悉 義隆 聚積 分別 拿下 面板 時序 控制 晶片 驅動 晶片 訂單 大單 也 是 雙方 合作 首 個 捷報 具 象徵 與 實質 效益 閱讀 全文 鴻海 平台 成員數 近 個 月 倍增 至 家未來 擬 舉辦 開發 者 大會 鴻海 技術長 暨 聯盟 軟體 平台 負責人 魏國章 昨日 透露 目前 平台 成員數 最近 一 個 月 倍增 已經 超過 家 未來 也 規劃 舉辦 開發者 大會 閱讀 全文 首 家 純網銀 正式 營運 樂天 首 推 兩 大 引擎 祭 台幣 天高利 定存 台灣 首 家 純網銀樂天國際銀行 昨日 正式 對 外 營運 為 台灣 開啟 了 純網銀 數位 金融 的 全新 紀元 樂天國際銀行 一 上線 就 推出 兩 大 殺手級 的 金融 創新 引擎 快樂 會員 制度 和 樂天 生態圈 其中 快樂 會員 制度 的 會員 可以 與 日本 同步 享有 樂天 點數 平台 堪稱 一 大 突破 此外 推出 台幣 天定存 提供 年利率 高達 倍 定存 的 年 利率 閱讀 全文 集邦 需求量 爆增 晶片 價格 調漲 集邦旗下光電研究處 表示 由於 蘋果 三星 等 品牌 計畫 在 年 推出 搭載 背光 顯示 的 筆電 平板 電視 等 產品 因此 提前 在 年 第四季 開始 拉貨 使 晶片 需求 暴增 進而 排擠 常規 晶片 產能 結構性 缺貨 下 部分 業者 已 調漲 非 核心 客戶 和 低 毛利 產品 的 晶片 價格 約 閱讀 全文 疫情 衝擊 比 金融 海嘯 還 慘 去年 上市 櫃 家數 創 近年 新 低 金管會 昨日 公布 去年 家數 上市櫃 合計 僅 家創 近年 